# Ham or Spam?

🎯 The goal of this challenge is to classify emails as spams (1) or normal emails (0)

🧹 First, you will apply cleaning techniques to these textual data

👩🏻‍🔬 Then, you will convert the cleaned texts into a numerical representation

✉️ Eventually, you will apply the ***Multinomial Naive Bayes*** model to classify each email as either a spam or a regular email.

## (0) The NTLK library (Natural Language Toolkit)

In [1]:
!pip install nltk

In [2]:
# When importing nltk for the first time, we need to also download a few built-in libraries

import nltk

nltk.download('stopwords')
nltk.download('punkt')
nltk.download('wordnet')
nltk.download('omw-1.4')

[nltk_data] Downloading package stopwords to
[nltk_data]     /home/raphaelsisso/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     /home/raphaelsisso/nltk_data...
[nltk_data]   Package punkt is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     /home/raphaelsisso/nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package omw-1.4 to
[nltk_data]     /home/raphaelsisso/nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!


True

In [3]:
import pandas as pd

df = pd.read_csv("https://wagon-public-datasets.s3.amazonaws.com/05-Machine-Learning/10-Natural-Language-Processing/ham_spam_emails.csv")
df.head()

text  spam
0  Subject: naturally irresistible your corporate...     1
1  Subject: the stock trading gunslinger  fanny i...     1
2  Subject: unbelievable new homes made easy  im ...     1
3  Subject: 4 color printing special  request add...     1
4  Subject: do not have money , get software cds ...     1

In [4]:
df.shape

(5728, 2)

## (1) Cleaning the (text) dataset

The dataset is made up of emails that are classified as ham [0] or spam[1]. You need to clean the dataset before training a prediction model.

### (1.1) Remove Punctuation

❓ Create a function to remove the punctuation. Apply it to the `text` column and add the output to a new column in the dataframe called `clean_text` ❓

In [5]:
import string # "string" module is already installed with Python
string.punctuation

'!"#$%&\'()*+,-./:;<=>?@[\\]^_`{|}~'

In [6]:
for punctuation in string.punctuation:
        df.text = df.text.str.replace(punctuation, '')

df.head()

/tmp/ipykernel_7106/409763878.py:2: FutureWarning: The default value of regex will change from True to False in a future version. In addition, single character regular expressions will *not* be treated as literal strings when regex=True.
  df.text = df.text.str.replace(punctuation, '')


text  spam
0  Subject naturally irresistible your corporate ...     1
1  Subject the stock trading gunslinger  fanny is...     1
2  Subject unbelievable new homes made easy  im w...     1
3  Subject 4 color printing special  request addi...     1
4  Subject do not have money  get software cds fr...     1

### (1.2) Lower Case

❓ Create a function to lowercase the text. Apply it to `clean_text` ❓

In [7]:
df.text = df.text.str.lower()

### (1.3) Remove Numbers

❓ Create a function to remove numbers from the text. Apply it to `clean_text` ❓

In [8]:
df['text'] = df['text'].str.replace(r'\d+', '', regex=True)
df

text  spam
0     subject naturally irresistible your corporate ...     1
1     subject the stock trading gunslinger  fanny is...     1
2     subject unbelievable new homes made easy  im w...     1
3     subject  color printing special  request addit...     1
4     subject do not have money  get software cds fr...     1
...                                                 ...   ...
5723  subject re  research and development charges t...     0
5724  subject re  receipts from visit  jim   thanks ...     0
5725  subject re  enron case study update  wow  all ...     0
5726  subject re  interest  david   please  call shi...     0
5727  subject news  aurora    update  aurora version...     0

[5728 rows x 2 columns]

### (1.4) Remove StopWords

❓ Create a function to remove stopwords from the text. Apply it to `clean_text`. ❓

In [9]:
df.text = df.text.astype(str)

In [10]:
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords 

stop_words = set(stopwords.words('english'))
df['text'] = df['text'].apply(lambda x: [word for word in word_tokenize(x) if word not in stop_words])
df

text  spam
0     [subject, naturally, irresistible, corporate, ...     1
1     [subject, stock, trading, gunslinger, fanny, m...     1
2     [subject, unbelievable, new, homes, made, easy...     1
3     [subject, color, printing, special, request, a...     1
4     [subject, money, get, software, cds, software,...     1
...                                                 ...   ...
5723  [subject, research, development, charges, gpg,...     0
5724  [subject, receipts, visit, jim, thanks, invita...     0
5725  [subject, enron, case, study, update, wow, day...     0
5726  [subject, interest, david, please, call, shirl...     0
5727  [subject, news, aurora, update, aurora, versio...     0

[5728 rows x 2 columns]

### (1.5) Lemmatize

❓ Create a function to lemmatize the text. Make sure the output is a single string, not a list of words. Apply it to `clean_text`. ❓

In [11]:
from nltk.stem import WordNetLemmatizer

df['clean_text'] = df['text'].apply(lambda x: [WordNetLemmatizer().lemmatize(word) for word in x])
df.head()

text  spam  \
0  [subject, naturally, irresistible, corporate, ...     1   
1  [subject, stock, trading, gunslinger, fanny, m...     1   
2  [subject, unbelievable, new, homes, made, easy...     1   
3  [subject, color, printing, special, request, a...     1   
4  [subject, money, get, software, cds, software,...     1   

                                          clean_text  
0  [subject, naturally, irresistible, corporate, ...  
1  [subject, stock, trading, gunslinger, fanny, m...  
2  [subject, unbelievable, new, home, made, easy,...  
3  [subject, color, printing, special, request, a...  
4  [subject, money, get, software, cd, software, ...

In [12]:
df['clean_text'] = df.clean_text.apply(lambda x: ' '.join([w for w in x]))
df.head()

text  spam  \
0  [subject, naturally, irresistible, corporate, ...     1   
1  [subject, stock, trading, gunslinger, fanny, m...     1   
2  [subject, unbelievable, new, homes, made, easy...     1   
3  [subject, color, printing, special, request, a...     1   
4  [subject, money, get, software, cds, software,...     1   

                                          clean_text  
0  subject naturally irresistible corporate ident...  
1  subject stock trading gunslinger fanny merrill...  
2  subject unbelievable new home made easy im wan...  
3  subject color printing special request additio...  
4  subject money get software cd software compati...

## (2) Bag-of-words Modelling

### (2.1) Digitizing the textual data into numbers

❓ Vectorize the `clean_text` to a Bag-of-Words representation with a default CountVectorizer. Save as `X_bow`. ❓

In [13]:
from sklearn.feature_extraction.text import CountVectorizer

# Initialize the CountVectorizer
vectorizer = CountVectorizer()

# Apply the vectorizer to the 'clean_text' column and store the result as X_bow
X_bow = vectorizer.fit_transform(df['clean_text'])

# Convert the result to a DataFrame for better readability (optional)
X_bow_df = pd.DataFrame(X_bow.toarray(), columns=vectorizer.get_feature_names_out())

# Show the resulting DataFrame
X_bow_df.head()

aa  aaa  aaaenerfax  aadedeji  aagrawal  aal  aaldous  aaliyah  aall  \
0   0    0           0         0         0    0        0        0     0   
1   0    0           0         0         0    0        0        0     0   
2   0    0           0         0         0    0        0        0     0   
3   0    0           0         0         0    0        0        0     0   
4   0    0           0         0         0    0        0        0     0   

   aanalysis  ...  zwzm  zxghlajf  zyban  zyc  zygoma  zymg  zzmacmac  zzn  \
0          0  ...     0         0      0    0       0     0         0    0   
1          0  ...     0         0      0    0       0     0         0    0   
2          0  ...     0         0      0    0       0     0         0    0   
3          0  ...     0         0      0    0       0     0         0    0   
4          0  ...     0         0      0    0       0     0         0    0   

   zzncacst  zzzz  
0         0     0  
1         0     0  
2         0     0  
3         0     0  
4         0     0  

[5 rows x 30962 columns]

In [14]:
pd.set_option('display.max_columns', None)  # Show all columns

X_bow_df.head()

aa  aaa  aaaenerfax  aadedeji  aagrawal  aal  aaldous  aaliyah  aall  \
0   0    0           0         0         0    0        0        0     0   
1   0    0           0         0         0    0        0        0     0   
2   0    0           0         0         0    0        0        0     0   
3   0    0           0         0         0    0        0        0     0   
4   0    0           0         0         0    0        0        0     0   

   aanalysis  aaron  aawesome  ab  aba  abacha  abacus  abahy  abaixo  \
0          0      0         0   0    0       0       0      0       0   
1          0      0         0   0    0       0       0      0       0   
2          0      0         0   0    0       0       0      0       0   
3          0      0         0   0    0       0       0      0       0   
4          0      0         0   0    0       0       0      0       0   

   abandon  abandoned  abandonment  abargain  abarr  abattoir  abb  abbas  \
0        0          0            0         0      0         0    0      0   
1        0          0            0         0      0         0    0      0   
2        0          0            0         0      0         0    0      0   
3        0          0            0         0      0         0    0      0   
4        0          0            0         0      0         0    0      0   

   abbestellen  abbott  abbreviated  abbreviation  abc  abcsearch  abdalla  \
0            0       0            0             0    0          0        0   
1            0       0            0             0    0          0        0   
2            0       0            0             0    0          0        0   
3            0       0            0             0    0          0        0   
4            0       0            0             0    0          0        0   

   abdallat  abdelnour  abdul  abdulla  abdullah  abeis  abel  abello  aber  \
0         0          0      0        0         0      0     0       0     0   
1         0          0      0        0         0      0     0       0     0   
2         0          0      0        0         0      0     0       0     0   
3         0          0      0        0         0      0     0       0     0   
4         0          0      0        0         0      0     0       0     0   

   abernathy  abetted  abeyance  abf  abhay  abide  abidjan  abiiity  abilene  \
0          0        0         0    0      0      0        0        0        0   
1          0        0         0    0      0      0        0        0        0   
2          0        0         0    0      0      0        0        0        0   
3          0        0         0    0      0      0        0        0        0   
4          0        0         0    0      0      0        0        0        0   

   ability  abit  abitibi  abklaeren  abl  able  abler  abliged  ablx  ably  \
0        0     0        0          0    0     0      0        0     0     0   
1        0     0        0          0    0     0      0        0     0     0   
2        0     0        0          0    0     0      0        0     0     0   
3        0     0        0          0    0     0      0        0     0     0   
4        0     0        0          0    0     0      0        0     0     0   

   abn  abnegate  abnormal  abnormality  aboard  abolish  abondantly  abook  \
0    0         0         0            0       0        0           0      0   
1    0         0         0            0       0        0           0      0   
2    0         0         0            0       0        0           0      0   
3    0         0         0            0       0        0           0      0   
4    0         0         0            0       0        0           0      0   

   aboriginal  abormalities  abort  abortive  abouts  aboutthis  aboutus  \
0           0             0      0         0       0          0        0   
1           0             0      0         0       0          0        0   
2           0             0      0       

### (2.2) Multinomial Naive Bayes Modelling

❓ Cross-validate a MultinomialNB model with the bag-of-words data. Score the model's accuracy. ❓

In [18]:
from sklearn.naive_bayes import MultinomialNB
from sklearn.model_selection import cross_val_score

multi = MultinomialNB()

accuracy = cross_val_score(multi, X_bow, df.spam, cv=5, scoring='accuracy').mean()
accuracy

0.9895252901681946

🏁 Congratulations !

💾 Don't forget to git add/commit/push your notebook...

🚀 ... and move on to the next challenge !